
# 🎓 초급 딥러닝 미션:
# 딥러닝 학교 – 마법 신경망으로 세계를 구하라!

---

## 🏰 배경 스토리

당신은 **AI 마법학교의 입학생**입니다.  
이 학교에서는 사람의 감정, 날씨, 질병을 예측하는 **마법 신경망**을 수련합니다.  
당신의 첫 수업은 **딥러닝 기초 수련**입니다.  
당신은 NumPy만으로 **마법 신경망**을 직접 구현하고, 다양한 마법서(Optimizer)를 실험하며,  
마지막엔 **PyTorch 마법 시스템**에 입문하게 됩니다.

---

## 🎯 미션 학습 목표

- 딥러닝 구조 및 원리 이해 (forward, loss, backward)
- 학습률 개념 실험
- 옵티마이저 종류 비교 (SGD, Momentum, RMSProp, Adam)
- 파이토치 기초 문법 학습 및 비교

---

## 🧩 미션 구성



### ✅ Part 1. 딥러닝 개요 퀴즈

1. 딥러닝에서 '신경망'이란 무엇을 모방한 것인가요?  
   a. 컴퓨터 회로  
   b. 인간 뇌의 뉴런 구조  
   c. 수학 공식  
   d. 로봇 제어기

   ### 정답 : b 

2. Backpropagation은 무엇을 계산하는 과정인가요?  
   a. 데이터 전처리  
   b. 예측 결과 시각화  
   c. 손실 함수의 그래디언트를 역방향으로 계산  
   d. 예측값을 정규화하는 함수

   ### 정답 : c 
   - 출력층부터 입력층까지 체인 룰을 따라 파라미터의 기울기를 계산하는 과정.



### ✅ Part 2. NumPy 기반 신경망 실습

#### 🎯 문제: XOR 문제를 NumPy만으로 푸는 2층 신경망을 직접 구현해보세요.

- 입력: 2차원 벡터 (ex: [0,1], [1,1])
- 출력: 0 또는 1
- 구조: 입력(2) → 은닉층(4, ReLU) → 출력층(1, Sigmoid)
- 손실 함수: Binary Cross Entropy

#### ✏️ 구현 항목
1. forward() – 순전파 계산
2. compute_loss() – 손실 계산
3. backward() – 역전파 계산 (Chain Rule 기반)
4. update_weights() – SGD 기반 파라미터 갱신 ==> 중요함!!
5. 학습률 변화 실험 (0.001 / 0.01 / 0.1)


In [7]:
import numpy as np 

def sigmoid(x) : return 1 / (1 + (np.exp(-x)))
def sigmoid_deriv(x) : return sigmoid(x) * (1 - sigmoid(x))
def relu(x) : return np.maximum(0, x)
def relu_deriv(x) : return (x > 0).astype(float)

#이진 교차 엔트로피 손실함수.
#이진 분류 문제에서 모델이 얼마나 잘 맞추고 있는지 평가하는 데 사용.
def binary_cross_entropy(y_pred, y_true):
    epsilon = 1e-8 #log 0이 에러가 날 수 있으니 epsilon을 살짝 더해서 log(0)이 발생하지 않도록 막기. 
    return - (y_true * np.log(y_pred + epsilon) + (1 - y_true) * np.log(1-y_pred + epsilon))

#수식이 이해가 잘 안된다.. 일단 그냥 외워야 하나 

def forward(x, W1, b1, W2, b2):
    z1 = x @ W1 + b1 #입 -> 은
    a1 = relu(z1)
    z2 = a1 @ W2 +b2  #은 -> 출
    a2 = sigmoid(z2)
    cache = (x, z1, a1, z2, a2) #순전파 결과를 저장해두는 핵심 역할. 
    return a2, cache

def backward(y_true, cache, W2):
    x, z1, a1, z2, a2 = cache #순전파에서 저장한 코드를 역전파에서 바로 쓰기 위해 꺼냄
    dz2 = a2 - y_true
    dW2 = a1.T @ dz2 #출력층 오차가 은닉층 출력에 얼마나 영향을 받았는지 계산해서 가중치 값을 조정.
    db2 = dz2 #편향

    da1 = dz2 @ W2.T #은닉층 출력에 대한 손실의 영향도 : 출력층에서 생긴 오차가 가중치를 타고 은닉층으로 흘러간다. 
    dz1 = da1 * relu_deriv(z1) #은닉층의 선형 입력 값 Z1에 대한 오차 기울기를 계산하는 단계 
    dW1 = x.T @ dz1 #은닉층 가중치에 대한 기울기 계산 
    db1 = dz1 

    return dW1, db1, dW2, db2



#XOR데이터 두 같이 다르면 1, 같으면 0 
X = np.array([[0,0], [0,1], [1,0], [1,1]])
y = np.array([[0], [1], [1], [0]])

np.random.seed(42)
W1 = np.random.randn(2,4)
b1 = np.zeros((1,4))
W2 = np.random.randn(4,1)
b2 = np.zeros((1,1))


# lr = 0.1 # 학습 실패
# lr = 0.01 # 학습 성공
lr = 0.001 # 학습 성공
epochs = 50000

for epoch in range(epochs):
    indices = np.random.permutation(len(X))
    total_loss = 0

    for i in indices:
        xi = X[i:i+1]
        yi = y[i:i+1]

        y_pred, cache = forward(xi, W1, b1, W2, b2)
        loss = binary_cross_entropy(y_pred, yi)
        print('loss=', loss)
        total_loss += loss

        dW1, db1, dW2, db2 = backward(yi, cache, W2)

        W1 -= lr * dW1
        b1 -= lr * db1
        W2 -= lr * dW2
        b2 -= lr * db2

    if epoch % 500 == 0:
        print(f"Epoch {epoch}, Avg Loss: {total_loss.mean():.4f}")

print("최종 예측:")
for xi in X:
    y_hat, _ = forward(xi.reshape(1, -1), W1, b1, W2, b2)
    print(f"입력: {xi}, 예측: {np.round(y_hat[0][0], 2)}")


loss= [[0.69314716]]
loss= [[1.49662041]]
loss= [[1.37755353]]
loss= [[0.10394782]]
Epoch 0, Avg Loss: 3.6713
loss= [[1.37531795]]
loss= [[1.48980825]]
loss= [[0.10491036]]
loss= [[0.69432156]]
loss= [[1.37137827]]
loss= [[0.69444454]]
loss= [[0.10520872]]
loss= [[1.48646962]]
loss= [[0.69453132]]
loss= [[0.1055945]]
loss= [[1.48427444]]
loss= [[1.36628736]]
loss= [[0.69499074]]
loss= [[0.10651291]]
loss= [[1.48001937]]
loss= [[1.36240265]]
loss= [[0.69544887]]
loss= [[1.36006374]]
loss= [[0.1079713]]
loss= [[1.47373645]]
loss= [[1.35584563]]
loss= [[1.46858325]]
loss= [[0.6966638]]
loss= [[0.10947716]]
loss= [[1.3520281]]
loss= [[0.10987892]]
loss= [[1.46500281]]
loss= [[0.69706563]]
loss= [[1.34823169]]
loss= [[1.46028236]]
loss= [[0.11139727]]
loss= [[0.69751787]]
loss= [[1.45819106]]
loss= [[0.11178582]]
loss= [[0.69759792]]
loss= [[1.34336301]]
loss= [[0.69771686]]
loss= [[1.45447777]]
loss= [[0.11267168]]
loss= [[1.33962526]]
loss= [[1.45001908]]
loss= [[0.11366759]]
loss= [[1.33


### ✅ Part 3. 다양한 옵티마이저 실험 (NumPy 구현 or 의사코드)

| Optimizer | 설명 |
|-----------|------|
| SGD | 가장 기본적인 경사하강법 |
| Momentum | 이전 기울기를 누적하여 반동 효과 부여 |
| RMSProp | 각 파라미터별 적응적 학습률 적용 |
| Adam | Momentum + RMSProp을 결합한 대표적 옵티마이저 |


아래 코드는 어떤 방식의 옵티마이저의 구현인지 답하시오.

### 정답 : Momentum
- 이전 그래디언트의 누적합을 현재 업데이트에 반영하여 속도와 안정성을 높이는 방식 

In [ ]:
# 💡 간단한 옵티마이저 의사코드 예시임. 
v = 0
v = beta * v + (1 - beta) * grad
w = w - learning_rate * v



### ✅ Part 4. PyTorch 입문 과제

이제부터는 AI 마법학교의 공식 프레임워크인 **PyTorch**를 배웁니다!

#### 🎯 미션: 위 XOR 문제를 PyTorch로 다시 풀어보세요.
- PyTorch로 간단한 학습 루프 예제 코드를 검색해서 찾아서 직접 작성해보세요.
- torch.nn.Linear, torch.ReLU, torch.Sigmoid, torch.BCELoss 등 사용
- torch.optim.SGD, Adam, RMSprop 등 Optimizer로 비교


In [14]:
import torch
import torch.nn as nn
import torch.optim as optim

X = torch.tensor([[0., 0.], [0., 1.], [1., 0.], [1., 1.]])
y = torch.tensor([[0.], [1.], [1.], [0.]])

model = nn.Sequential(
    nn.Linear(2, 4), #입력 2차원, 은닉층 4차원
    nn.ReLU(), #비선형성 추가
    nn.Linear(4, 1), #은닉층 4차원 출력 1차원 
    nn.Sigmoid() #출력값을 0~1 사이 확률로 변환 
) #Sequential : 여러층을 순차적으로 연결하는 모델 

criterion = nn.BCELoss() #이진분류에서 가장 많이 쓰는 손실 함수 
optimizer = optim.Adam(model.parameters(), lr=0.01)
#Adam : 인기 많은 옵티마이저(SGD보다 안정적, 자동으로 학습률 조정) 

for epoch in range(10000):
    optimizer.zero_grad() #gradient초기화/backward 호줄시 gradient가 누적되기 때문에

    outputs = model(X)
    loss = criterion(outputs, y)
    loss.backward()
    optimizer.step()

    if epoch % 1000 == 0:
        print(f"Epoch {epoch}, Loss: {loss.item():.4f}")

print("최종 예측 결과:")
print(torch.round(model(X)).detach())



ModuleNotFoundError: No module named 'torch'


## 🏁 마무리 퀴즈

1. 학습률이 너무 크면 발생할 수 있는 문제는?
   - a. 과적합  
   - b. 손실 발산  
   - c. 더 정밀한 학습  
   - d. 정확도가 무조건 올라감
   ###  정답 : b. 손실 발산 
   - 너무 큰 학습률은 최적점을 지나쳐 손실이 폭증할 수 있다.

2. Adam 옵티마이저는 어떤 두 가지 개념을 결합한 것인가요?
   - a. LSTM + GRU  
   - b. SGD + Dropout  
   - c. Momentum + RMSProp  
   - d. SGD + AdaGrad

   ### 정답 : C Momentum + RMSProp
   - Adam은 1차 모멘트(Momentum) + 2차 모멘트(RMSProp)를 동시에 고려한다. 




## 🎁 보너스 미션 (선택)

- 직접 XOR이 아닌 make_moons, make_circles 등의 데이터셋으로 실험해보세요.
- 은닉층의 노드 수를 바꿔가며 학습 성능을 비교해보세요.

